In [43]:
%pip install pymongo psycopg2-binary pandas python-dotenv


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.3 -> 26.0.1
[notice] To update, run: C:\Users\HP\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [44]:
import hashlib
from datetime import datetime


In [45]:

import pymongo
from pymongo import MongoClient

try:
    # Connect to local MongoDB
    client = MongoClient("mongodb://localhost:27017/")

    # Test server connection
    client.admin.command("ping")

    print("MongoDB connection successful!")

except Exception as e:
    print("Connection failed:", e)

MongoDB connection successful!


In [46]:
from pymongo import MongoClient

# Connect to local MongoDB
client = MongoClient("mongodb://localhost:27017/")

# Create or access database
db = client["commercepulse"]

# Create or access collection
collection = db["events_raw_data"]




In [47]:
import os
import json
from pymongo import MongoClient

# Connecting to local MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["commercepulse"]           # database name
collection = db["events_raw"]     # collection name

# Inserting path to data\bootstrap folder containing JSON files

folder_path = r"C:\Users\HP\Desktop\commercepulse_data_pack\data\bootstrap" 

# 3. Loop through all JSON files

for filename in os.listdir(folder_path):
    if filename.endswith(".json"):
        file_path = os.path.join(folder_path, filename)
        
        with open(file_path, "r") as file:
            data = json.load(file)

            # Ensure we have a list for insert_many
            if isinstance(data, dict):
                data = [data]

            # Insert data into MongoDB as-is
            collection.insert_many(data)

        print(f"Inserted {filename} successfully")

print("All JSON files have been inserted into events_raw_data collection!")


All JSON files have been inserted into events_raw_data collection!


In [48]:
print("Collections in database:", db.list_collection_names())

Collections in database: ['events_raw']


In [49]:
# Confirm succesful importation and understanding our data by fetching all documents in the collection
# Fetch all documents
documents = collection.find() 
# Loop through and print each document
for doc in documents:
    print(doc)

{'_id': ObjectId('6993a3ed34b30965e4ed2e1f'), 'order_id': 'ORD-000001', 'created_at': '2023-10-10T22:31:55Z', 'buyerEmail': 'user677@pulse.africa', 'buyerPhone': '+2348026726926', 'customerId': None, 'line_items': [{'sku': 'SKU-0155', 'quantity': 3, 'unit_price': 9000}, {'sku': 'SKU-0098', 'quantity': 3, 'unit_price': 6700}, {'sku': 'SKU-0065', 'quantity': 1, 'unit_price': 2500}, {'sku': 'SKU-0000', 'quantity': 3, 'unit_price': 2700}], 'totalAmount': 57700, 'currencyCode': 'NGN', 'state': 'Kano', 'address': {'line1': '77 GRA Rd', 'city': 'Kano', 'country': 'NG'}, 'event_id': 'c6ada6bdd20277907518d23a443c11066703883fafb9babc247458e974cab964', 'event_time': datetime.datetime(2026, 2, 17, 0, 16, 32, 832000), 'event_type': 'historical_order', 'ingested_at': datetime.datetime(2026, 2, 17, 0, 16, 32, 832000), 'payload': {'order_id': 'ORD-000001', 'created_at': '2023-10-10T22:31:55Z', 'buyerEmail': 'user677@pulse.africa', 'buyerPhone': '+2348026726926', 'customerId': None, 'line_items': [{'sk

In [50]:
# Confirming that eah data include the required fields
# Define required fields
required_fields = ["event_id", "event_type", "event_time", "vendor", "payload", "ingestion_at"]

# Fetch all documents
documents = collection.find()

# Track documents missing required fields
missing_fields_docs = []

for doc in documents:
    missing = [field for field in required_fields if field not in doc]
    if missing:
        missing_fields_docs.append({"_id": doc["_id"], "missing_fields": missing})

# Report results
if not missing_fields_docs:
    print("All documents contain all required fields!")
else:
    print("Some documents are missing fields:")
    for item in missing_fields_docs:
        print(f"Document ID: {item['_id']}, Missing: {item['missing_fields']}")


Some documents are missing fields:
Document ID: 6993a3ed34b30965e4ed2e1f, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e20, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e21, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e22, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e23, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e24, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e25, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e26, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e27, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e28, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e29, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e2a, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e2b, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e2c, Missing: ['ingestion_at']
Document ID: 6993a3ed34b30965e4ed2e2d, Missing: ['inges

In [51]:
documents = collection.find()  # fresh cursor

for doc in documents:
    update_needed = {}

    # Wrapping original record in payload if missing
    if "payload" not in doc:
        original = doc.copy()
        original.pop("_id", None)
        update_needed["payload"] = original

    # Creating deterministic event_id hash
    if "event_id" not in doc:
        payload_str = str(update_needed.get("payload", doc))
        update_needed["event_id"] = hashlib.sha256(payload_str.encode()).hexdigest()

    # Adding other missing fields
    if "event_type" not in doc:
        update_needed["event_type"] = "historical_order"
    if "event_time" not in doc:
        update_needed["event_time"] = datetime.utcnow()
    if "vendor" not in doc:
        update_needed["vendor"] = "unknown"
    if "ingested_at" not in doc:
        update_needed["ingested_at"] = datetime.utcnow()

    if update_needed:
        collection.update_one({"_id": doc["_id"]}, {"$set": update_needed})

print("All documents updated with required fields")


All documents updated with required fields


In [ ]:

documents = collection.find()

required_fields = ["event_id", "event_type", "event_time", "vendor", "payload", "ingested_at"]
missing_fields_docs = []

for doc in documents:
    missing = [f for f in required_fields if f not in doc]
    if missing:
        missing_fields_docs.append({"_id": doc["_id"], "missing": missing})

if not missing_fields_docs:
    print("All documents now include all required fields!")
else:
    print("Some documents are still missing fields:")
    for item in missing_fields_docs:
        print(f"Document ID: {item['_id']}, Missing: {item['missing']}")



All documents now include all required fields!
